<a href="https://colab.research.google.com/github/AshishGusain17/Grad-CAM-implementation/blob/master/tf_explain_methods.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
!pip install tf-explain

from keras.preprocessing.image import ImageDataGenerator
import numpy as np
import tensorflow as tf
import tf_explain

INPUT_SHAPE = (28, 28, 1)
NUM_CLASSES = 10

# AVAILABLE_DATASETS
# "mnist": tf.keras.datasets.mnist,
# "fashion_mnist": tf.keras.datasets.fashion_mnist,
# tf.keras.datasets.cifar100.load_data(label_mode="fine")

     |████████████████████████████████| 51kB 2.5MB/s 


Using TensorFlow backend.


In [ ]:

# Load dataset
dataset = tf.keras.datasets.mnist
(train_images, train_labels), (test_images, test_labels) = dataset.load_data()
print(train_images.shape , train_labels.shape , test_images.shape , test_labels.shape)

11493376/11490434 [==============================] - 0s 0us/step
(60000, 28, 28) (60000,) (10000, 28, 28) (10000,)


In [ ]:

# Convert from (28, 28) images to (28, 28, 1)
train_images = train_images[..., tf.newaxis].astype("float32") / 255.0
test_images = test_images[..., tf.newaxis].astype("float32") / 255.0
print(train_images.shape , test_images.shape)


(60000, 28, 28, 1) (10000, 28, 28, 1)


In [ ]:
# One hot encore labels 0, 1, .., 9 to [0, 0, .., 1, 0, 0]
train_labels = tf.keras.utils.to_categorical(train_labels, num_classes=NUM_CLASSES)
test_labels = tf.keras.utils.to_categorical(test_labels, num_classes=NUM_CLASSES)
print(train_labels.shape , test_labels.shape)

(60000, 10) (10000, 10)


In [ ]:
augs_gen = ImageDataGenerator(
            zoom_range=0.2, 
            rotation_range=10,
            width_shift_range=0.3, 
            height_shift_range=0.3,
            shear_range=0.4,
            horizontal_flip=True,
            fill_mode='nearest',

            featurewise_center=False,  
            samplewise_center=False, 
            featurewise_std_normalization=False,  
            samplewise_std_normalization=False,  
            zca_whitening=False,  
        ) 

augs_gen.fit(train_images)

In [ ]:
img_input = tf.keras.Input(INPUT_SHAPE)

x = tf.keras.layers.Conv2D(filters=32, kernel_size=(3, 3), activation="relu" , name="layer1")(img_input)
x = tf.keras.layers.Conv2D(filters=64, kernel_size=(3, 3), activation="relu", name="layer2")(x)
x = tf.keras.layers.MaxPool2D(pool_size=(2, 2))(x)

x = tf.keras.layers.Dropout(0.25)(x)
x = tf.keras.layers.Flatten()(x)

x = tf.keras.layers.Dense(128, activation="relu")(x)
x = tf.keras.layers.Dropout(0.5)(x)

x = tf.keras.layers.Dense(NUM_CLASSES, activation="softmax")(x)

model = tf.keras.Model(img_input, x)
model.summary()

Model: "model_18"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_3 (InputLayer)         [(None, 28, 28, 1)]       0         
_________________________________________________________________
layer1 (Conv2D)              (None, 26, 26, 32)        320       
_________________________________________________________________
layer2 (Conv2D)              (None, 24, 24, 64)        18496     
_________________________________________________________________
max_pooling2d_2 (MaxPooling2 (None, 12, 12, 64)        0         
_________________________________________________________________
dropout_4 (Dropout)          (None, 12, 12, 64)        0         
_________________________________________________________________
flatten_2 (Flatten)          (None, 9216)              0         
_________________________________________________________________
dense_4 (Dense)              (None, 128)               117

In [ ]:

# Select a subset of the validation data to examine
# Here, we choose 5 elements with one hot encoded label "0" == [1, 0, 0, .., 0]
validation_class_zero = (
    np.array(
        [
            el
            for el, label in zip(test_images, test_labels)
            if np.all(np.argmax(label) == 0)
        ][0:5]
    ),
    None,
)
# Select a subset of the validation data to examine
# Here, we choose 5 elements with one hot encoded label "4" == [0, 0, 0, 0, 1, 0, 0, 0, 0, 0]
validation_class_four = (
    np.array(
        [
            el
            for el, label in zip(test_images, test_labels)
            if np.all(np.argmax(label) == 4)
        ][0:5]
    ),
    None,
)

# Instantiate callbacks
# class_index value should match the validation_data selected above
callbacks = [
    tf_explain.callbacks.GradCAMCallback(validation_class_zero, class_index=0, layer_name="layer2"),
    tf_explain.callbacks.GradCAMCallback(validation_class_four, class_index=4, layer_name="layer2"),

    tf_explain.callbacks.ActivationsVisualizationCallback(validation_class_zero, layers_name=["layer2"]),
    tf_explain.callbacks.ActivationsVisualizationCallback(validation_class_four, layers_name=["layer2"]),

    tf_explain.callbacks.SmoothGradCallback(validation_class_zero, class_index=0, num_samples=15, noise=1.0),
    tf_explain.callbacks.SmoothGradCallback(validation_class_four, class_index=4, num_samples=15, noise=1.0),

    tf_explain.callbacks.IntegratedGradientsCallback(validation_class_zero, class_index=0, n_steps=10),
    tf_explain.callbacks.IntegratedGradientsCallback(validation_class_four, class_index=4, n_steps=10),

    tf_explain.callbacks.VanillaGradientsCallback(validation_class_zero, class_index=0),
    tf_explain.callbacks.VanillaGradientsCallback(validation_class_four, class_index=4),

    tf_explain.callbacks.GradientsInputsCallback(validation_class_zero, class_index=0),
    tf_explain.callbacks.GradientsInputsCallback(validation_class_four, class_index=4),
]


In [ ]:
%reload_ext tensorboard

%tensorboard --logdir logs

In [ ]:
opt1 = tf.keras.optimizers.Adam(learning_rate=0.001)
# opt1 = tf.keras.optimizers.SGD(learning_rate=0.01)
# opt1 = tf.keras.optimizers.RMSprop(learning_rate=0.001)
# opt1 = tf.keras.optimizers.Adagrad(learning_rate=0.001)


model.compile(optimizer=opt1, loss="categorical_crossentropy", metrics=["accuracy"])



# Start training
# model.fit(train_images, train_labels, epochs=200, batch_size=32, callbacks=callbacks)


history = model.fit_generator(
    augs_gen.flow(train_images,train_labels,batch_size=32),
    validation_data  = (test_images,test_labels),
    # steps_per_epoch=len(x_train),
    epochs =325, 
    verbose = 1,
    callbacks=callbacks
)


In [ ]:
0.001    adam
loss: 0.4919 - accuracy: 0.8458 - val_loss: 0.1386 - val_accuracy: 0.9542



0.01    sgd
loss: 0.7088 - accuracy: 0.7597 - val_loss: 0.2758 - val_accuracy: 0.9064



0.001    rmsprop
loss: 0.7438 - accuracy: 0.7749 - val_loss: 0.3535 - val_accuracy: 0.9067



